# Objective and key steps

Input:
A table that conatains the historical pricing data

Output:
A table that still contains the historical pricing data but with additional columns/variables for price percentage change over different time windows 

Key steps:

1. Data import -  the pricing data through Yahoo api and light-touch cleanse
2. Feature creation - 1. percentage change on closing price for one and 2.multiple time windows


In [18]:
import pandas as pd
import numpy as np
import yfinance as yf
import datetime
import ticker_data_prep
import visualisation
import datadq

# Data import

In [2]:
#input for data download
tkr='TSLA'
timespan=1800

In [3]:
#use yfinance to download ticker data, interval - daily
today=datetime.date.today()
start_date=(today-datetime.timedelta(days=timespan)).strftime('%Y-%m-%d')
enddate=today.strftime('%Y-%m-%d')
data=yf.download(tkr,start_date,enddate)
data.head(2)

2021-01-31 23:11:37,010 - NumExpr defaulting to 8 threads.


[*********************100%***********************]  1 of 1 completed


Open       High        Low      Close  Adj Close    Volume
Date                                                                       
2016-02-29  38.480000  39.270000  37.844002  38.386002  38.386002  22495000
2016-03-01  38.849998  39.189999  36.540001  37.270000  37.270000  33561000

Light touch data cleansing

In [4]:
df_stock=ticker_data_prep.tkr_data_main(ticker=tkr,timescope=timespan,datatype='daily')
df_stock.head(2)

2021-01-31 23:11:37,159 - Getting data for TSLA


[*********************100%***********************]  1 of 1 completed

2021-01-31 23:11:37,259 - Column names updated with ticker identifier
2021-01-31 23:11:37,260 - Exporting stock daily data for TSLA
2021-01-31 23:11:37,278 - row count is 1240
2021-01-31 23:11:37,279 - column count is 7
2021-01-31 23:11:37,279 - Data has been exported to raw_stock_ticker_data/equity_TSLA_daily.csv 



             Open   High        Low      Close  Adj Close    Volume ticker
Date                                                                      
2016-02-29  38.48  39.27  37.844002  38.386002  38.386002  22495000   TSLA


tsla_open  tsla_high   tsla_low  tsla_close  tsla_adj_close  \
Date                                                                      
2016-02-29  38.480000  39.270000  37.844002   38.386002       38.386002   
2016-03-01  38.849998  39.189999  36.540001   37.270000       37.270000   

            tsla_volume tsla_ticker  
Date                                 
2016-02-29   22495000.0        TSLA  
2016-03-01   33561000.0        TSLA

In [5]:
#get the column names for open, high,low and close price
for c in df_stock.columns:
    if 'open' in c:
        colnm_open=c
    if 'high' in c:
        colnm_high=c
    if 'low' in c:
        colnm_low=c
    if 'close' in c:
        colnm_close=c

# Feature creation

percentage change for one time window

In [6]:
window=1 
colnm_pct_chg='pct_chg'+'_'+str(window)
df_stock[colnm_pct_chg]=df_stock[colnm_close].pct_change(window)

In [7]:
df_stock[colnm_pct_chg]

Date
2016-02-29         NaN
2016-03-01   -0.029073
2016-03-02    0.010679
2016-03-03    0.039291
2016-03-04    0.027077
                ...   
2021-01-25    0.040348
2021-01-26    0.002600
2021-01-27   -0.021436
2021-01-28   -0.033246
2021-01-29   -0.050154
Name: pct_chg_1, Length: 1240, dtype: float64

In [8]:
df_stock.head(5)

tsla_open  tsla_high   tsla_low  tsla_close  tsla_adj_close  \
Date                                                                      
2016-02-29  38.480000  39.270000  37.844002   38.386002       38.386002   
2016-03-01  38.849998  39.189999  36.540001   37.270000       37.270000   
2016-03-02  36.745998  37.703999  36.299999   37.667999       37.667999   
2016-03-03  37.655998  39.484001  36.844002   39.147999       39.147999   
2016-03-04  39.599998  40.806000  39.500000   40.208000       40.208000   

            tsla_volume tsla_ticker  pct_chg_1  
Date                                            
2016-02-29   22495000.0        TSLA        NaN  
2016-03-01   33561000.0        TSLA  -0.029073  
2016-03-02   24312000.0        TSLA   0.010679  
2016-03-03   24145000.0        TSLA   0.039291  
2016-03-04   32445500.0        TSLA   0.027077

percentage change for multiple time windows

In [9]:
windows=[i for i in range (1,61)]
for w in windows:
    colnm_pct_chg='pct_chg'+'_'+str(w)
    df_stock[colnm_pct_chg]=df_stock[colnm_close].pct_change(w)
df_stock.head(5)

tsla_open  tsla_high   tsla_low  tsla_close  tsla_adj_close  \
Date                                                                      
2016-02-29  38.480000  39.270000  37.844002   38.386002       38.386002   
2016-03-01  38.849998  39.189999  36.540001   37.270000       37.270000   
2016-03-02  36.745998  37.703999  36.299999   37.667999       37.667999   
2016-03-03  37.655998  39.484001  36.844002   39.147999       39.147999   
2016-03-04  39.599998  40.806000  39.500000   40.208000       40.208000   

            tsla_volume tsla_ticker  pct_chg_1  pct_chg_2  pct_chg_3  ...  \
Date                                                                  ...   
2016-02-29   22495000.0        TSLA        NaN        NaN        NaN  ...   
2016-03-01   33561000.0        TSLA  -0.029073        NaN        NaN  ...   
2016-03-02   24312000.0        TSLA   0.010679  -0.018705        NaN  ...   
2016-03-03   24145000.0        TSLA   0.039291   0.050389   0.019851  ...   
2016-03-04   32445500.0        TSLA   0.027077   0.067431   0.078830  ...   

            pct_chg_51  pct_chg_52  pct_chg_53  pct_chg_54  pct_chg_55  \
Date                                                                     
2016-02-29         NaN         NaN         NaN         NaN         NaN   
2016-03-01         NaN         NaN         NaN         NaN         NaN   
2016-03-02         NaN         NaN         NaN         NaN         NaN   
2016-03-03         NaN         NaN         NaN         NaN         NaN   
2016-03-04         NaN         NaN         NaN         NaN         NaN   

            pct_chg_56  pct_chg_57  pct_chg_58  pct_chg_59  pct_chg_60  
Date                                                                    
2016-02-29         NaN         NaN         NaN         NaN         NaN  
2016-03-01         NaN         NaN         NaN         NaN         NaN  
2016-03-02         NaN         NaN         NaN         NaN         NaN  
2016-03-03         NaN         NaN         NaN         NaN         NaN  
2016-03-04         NaN         NaN         NaN         NaN         NaN  

[5 rows x 67 columns]

In [10]:
df_stock[list(filter(lambda x:'pct_chg' in x,df_stock.columns))].describe()

pct_chg_1    pct_chg_2    pct_chg_3    pct_chg_4    pct_chg_5  \
count  1239.000000  1238.000000  1237.000000  1236.000000  1235.000000   
mean      0.003110     0.006307     0.009586     0.012931     0.016228   
std       0.036454     0.052195     0.064808     0.076787     0.086749   
min      -0.210628    -0.212982    -0.339175    -0.355597    -0.430459   
25%      -0.014004    -0.019384    -0.024041    -0.027149    -0.030896   
50%       0.001458     0.004778     0.007096     0.008152     0.011369   
75%       0.019382     0.030972     0.039905     0.047599     0.053639   
max       0.198949     0.363512     0.384279     0.526808     0.564756   

         pct_chg_6    pct_chg_7    pct_chg_8    pct_chg_9   pct_chg_10  ...  \
count  1234.000000  1233.000000  1232.000000  1231.000000  1230.000000  ...   
mean      0.019449     0.022647     0.025880     0.029161     0.032412  ...   
std       0.095328     0.102763     0.110161     0.117591     0.124378  ...   
min      -0.440255    -0.405888    -0.486524    -0.501449    -0.518052  ...   
25%      -0.031674    -0.034798    -0.036167    -0.042682    -0.047368  ...   
50%       0.013324     0.015186     0.018077     0.020103     0.022199  ...   
75%       0.062243     0.069185     0.073521     0.084550     0.087727  ...   
max       0.589656     0.570518     0.605893     0.639734     0.658833  ...   

        pct_chg_51   pct_chg_52   pct_chg_53   pct_chg_54   pct_chg_55  \
count  1189.000000  1188.000000  1187.000000  1186.000000  1185.000000   
mean      0.166915     0.170166     0.173464     0.176786     0.180157   
std       0.357171     0.361656     0.366286     0.370874     0.375837   
min      -0.349221    -0.346968    -0.350876    -0.361429    -0.382777   
25%      -0.087110    -0.083955    -0.084221    -0.080988    -0.084394   
50%       0.056992     0.062438     0.061184     0.066263     0.065917   
75%       0.287980     0.295764     0.298856     0.300766     0.307892   
max       1.754767     1.728792     1.739630     1.780566     1.769235   

        pct_chg_56   pct_chg_57   pct_chg_58   pct_chg_59   pct_chg_60  
count  1184.000000  1183.000000  1182.000000  1181.000000  1180.000000  
mean      0.183603     0.186921     0.190342     0.193709     0.197139  
std       0.380986     0.385314     0.390373     0.395353     0.400502  
min      -0.380641    -0.368401    -0.397493    -0.388865    -0.404058  
25%      -0.084300    -0.083855    -0.086127    -0.083820    -0.084930  
50%       0.065632     0.069201     0.070410     0.071205     0.076175  
75%       0.317473     0.322758     0.324422     0.328903     0.324263  
max       1.789189     1.734434     1.837744     1.700607     1.813269  

[8 rows x 60 columns]

# Bring some visuals

In [11]:
df_stock.head(2)

tsla_open  tsla_high   tsla_low  tsla_close  tsla_adj_close  \
Date                                                                      
2016-02-29  38.480000  39.270000  37.844002   38.386002       38.386002   
2016-03-01  38.849998  39.189999  36.540001   37.270000       37.270000   

            tsla_volume tsla_ticker  pct_chg_1  pct_chg_2  pct_chg_3  ...  \
Date                                                                  ...   
2016-02-29   22495000.0        TSLA        NaN        NaN        NaN  ...   
2016-03-01   33561000.0        TSLA  -0.029073        NaN        NaN  ...   

            pct_chg_51  pct_chg_52  pct_chg_53  pct_chg_54  pct_chg_55  \
Date                                                                     
2016-02-29         NaN         NaN         NaN         NaN         NaN   
2016-03-01         NaN         NaN         NaN         NaN         NaN   

            pct_chg_56  pct_chg_57  pct_chg_58  pct_chg_59  pct_chg_60  
Date                                                                    
2016-02-29         NaN         NaN         NaN         NaN         NaN  
2016-03-01         NaN         NaN         NaN         NaN         NaN  

[2 rows x 67 columns]

Boxplot for osciliation

In [13]:
visualisation.visual_boxplot(
        data=df_stock,
        col_keys=['pct_chg'],
        col_no_keys=[],
        ht=20000,
        wdth=1000,
        mtd='subplot'
            )

Barchart for monthly return

In [15]:
#Create a year-month column for the groupby
df_stock['year']=df_stock.index.year
df_stock['month']=df_stock.index.month
df_stock['year-month']=df_stock.apply(lambda x:str(x['year'])+'-'+str(x['month']),axis=1)

In [20]:
#Prepare a dataset for the monthly roll-up visualsiation, df_stcok_monthly_sum
metrics=[list(filter(lambda x:'pct_chg_1' in x,df_stock.columns))[0]]
stats=['sum','std','max','min']
dict_agg_metrics={m:stats for m in metrics}
df_stock_monthly_sum=df_stock.groupby('year-month',as_index=False).agg(dict_agg_metrics)
datadq.drop_column_multi_index(df_stock_monthly_sum)
df_stock_monthly_sum.head(2)

year-month  pct_chg_1_sum  pct_chg_1_std  pct_chg_1_max  pct_chg_1_min
0    2016-10      -0.027428       0.019841       0.047395      -0.035786
1    2016-11      -0.038493       0.021170       0.036040      -0.037707

In [22]:
visualisation.visual_bar_chart(
            data=df_stock_monthly_sum,
            col_keys=['sum'],
            col_no_keys=[],
            ht=1400,
            wdth=800,
            col_x='year-month',
            mtd='subplot'
)

Thanks for watching :)